In [1]:
import matplotlib.pyplot as plt
import numpy as np
import scipy.optimize as optimize
import time

from kinematics import *

%config InlineBackend.figure_format='retina'
np.set_printoptions(edgeitems=30, linewidth=1000, formatter={'float': '{: 0.4f}'.format})

# Helpers

In [2]:
def slerp(q0, q1, h):
    theta = q0.q.T @ q1.q
    q = np.sin((1.0 - h) * theta) * q0.q / np.sin(theta) \
      + np.sin(h * theta) / np.sin(theta) * q1.q
    return Quaternion(q).normalized()

def get_ang_vel_from_q0_to_q1(q0, q1, dt):
    return 2.0 * q0.conj().prod(Quaternion(q1.q - q0.q)).v / dt

def euler_to_quaternion(roll, pitch, yaw):
    qw = np.cos(roll/2) * np.cos(pitch/2) * np.cos(yaw/2) + np.sin(roll/2) * np.sin(pitch/2) * np.sin(yaw/2)
    qx = np.sin(roll/2) * np.cos(pitch/2) * np.cos(yaw/2) - np.cos(roll/2) * np.sin(pitch/2) * np.sin(yaw/2)
    qy = np.cos(roll/2) * np.sin(pitch/2) * np.cos(yaw/2) + np.sin(roll/2) * np.cos(pitch/2) * np.sin(yaw/2)
    qz = np.cos(roll/2) * np.cos(pitch/2) * np.sin(yaw/2) - np.sin(roll/2) * np.sin(pitch/2) * np.cos(yaw/2)
    return Quaternion([qw, qx, qy, qz])

def quaternion_to_euler(q):
    t0 = 2.0 * (q[0] * q[1] + q[2] * q[3])
    t1 = 1.0 - 2.0 * (q[1] * q[1] + q[2] * q[2])
    roll = np.arctan2(t0, t1)[0]
    t2 = 2.0 * (q[0] * q[2] - q[3] * q[1])
    t2 = 1.0 if t2 > 1.0 else t2
    t2 = -1.0 if t2 < -1.0 else t2
    pitch = np.arcsin(t2)[0]
    t3 = 2.0 * (q[0] * q[3] + q[1] * q[2])
    t4 = 1.0 - 2.0 * (q[2] * q[2] + q[3] * q[3])
    yaw = np.arctan2(t3, t4)[0]
    return roll, pitch, yaw

def generate_orientations(q0, q1, N):
    return [slerp(q0, q1, h) for h in np.linspace(0.0, 1.0, N)]

def get_w_and_a_from_orientation_sequence(orientations, dt = 0.01):
    o_prev = orientations[0]
    angular_velocities = []
    accelerations = []
    for o in orientations[0:]:
        angular_velocities.append(get_ang_vel_from_q0_to_q1(o_prev, o, dt))
        acc_bf_meas = o.Rm().T @ np.array([[0.0], [0.0], [9.81]])
        accelerations.append(acc_bf_meas.flatten())
        o_prev = o
    return np.array(angular_velocities), np.array(accelerations)

def generate_inertial_measurements_between_orientations(fromOrientation, toOrientation, N_samples, dt):
    orientations = generate_orientations(fromOrientation, toOrientation, N_samples)
    angular_velocities, accelerations = get_w_and_a_from_orientation_sequence(orientations, dt)
    
    return angular_velocities, accelerations

def build_matrix_and_bias_for_sensor_imperfections(imperfections):
    if len(imperfections) == 9:
        KX, KY, KZ, NOX, NOY, NOZ, BX, BY, BZ = imperfections
    else:
        KX, KY, KZ, NOX, NOY, NOZ, BX, BY, BZ, _, _, _ = imperfections
    Ca = np.array([[1.0 + KX, NOY, NOZ], 
                  [0.0, 1.0 + KY, NOX], 
                  [0.0, 0.0, 1.0 + KZ]])
    ba = np.array([BX, BY, BZ])
    
    return Ca, ba

def get_Rm_gyro_to_acc(imperfections):
    return np.eye(3) + skew(imperfections[-3:])

def get_Rm_acc_to_gyro(imperfections):
    return np.eye(3) - skew(imperfections[-3:])

def calibrate_data(measurements, theta):
    # meas = C @ (w + b) => w_true = inv(C) @ meas - b
    C, b = build_matrix_and_bias_for_sensor_imperfections(theta)
    C = np.linalg.inv(C)
    calibrated_measurements = np.copy(measurements)
    for measurement in calibrated_measurements:
        measurement[:] = C @ measurement - C @ b
    return calibrated_measurements

# Synthesis of gyroscope and accelerometer data during rotations

In [3]:
def generate_data(start_roll, start_pitch, start_yaw, yaw_increment, theta_acc, theta_gyr, 
                  N_samples = 100, dt=0.01, randomized = False):
       
    zero_epoch_orientation = euler_to_quaternion(start_roll, start_pitch, start_yaw)
    ang_velocities, accelerations = generate_inertial_measurements_between_orientations(
                zero_epoch_orientation, zero_epoch_orientation, N_samples, dt)
    standstill = np.ones(len(ang_velocities))
    
    
    roll, pitch, yaw = start_roll, start_pitch, start_yaw
    roll_prev, pitch_prev, yaw_prev = start_roll, start_pitch, start_yaw
    for pitch in np.linspace(start_pitch + np.pi/4, start_pitch + np.pi, 4):
        for roll in np.linspace(start_roll, start_roll + 2 * np.pi, 6):
            if randomized:
                roll  += np.deg2rad(np.random.randint(60)) * np.random.choice([-1, 0, 1])
                pitch  += np.deg2rad(np.random.randint(45)) * np.random.choice([-1, 0, 1])
            yaw += yaw_increment
            
            # generate data through rotation
            fromOrientation = euler_to_quaternion(roll_prev, pitch_prev, yaw_prev)
            toOrientation = euler_to_quaternion(roll, pitch, yaw)
            ang, acc = generate_inertial_measurements_between_orientations(
                fromOrientation, toOrientation, N_samples, dt)
            
            ang_velocities = np.concatenate((ang_velocities, ang), axis=0)
            accelerations = np.concatenate((accelerations, acc), axis=0)
            standstill = np.concatenate((standstill, np.zeros(N_samples)), axis=0)

            # generate data through standstill
            ang, acc = generate_inertial_measurements_between_orientations(
                toOrientation, toOrientation, N_samples, dt)
            
            ang_velocities = np.concatenate((ang_velocities, ang), axis=0)
            accelerations = np.concatenate((accelerations, acc), axis=0)
            standstill = np.concatenate((standstill, np.ones(N_samples)), axis=0)
            
            roll_prev, pitch_prev, yaw_prev = roll, pitch, yaw
    
    orientation_true_start = euler_to_quaternion(start_roll, start_pitch, start_yaw)
    orientations_true = []
    orientations_true.append(orientation_true_start.q)
    q = orientation_true_start
    for w in ang_velocities:
        q_upd = Quaternion.exactFromOmega((w) * dt)
        q = q.prod(q_upd)
        orientations_true.append(q.q)
    
    Ca, ba = build_matrix_and_bias_for_sensor_imperfections(theta_acc)
    Cg, bg = build_matrix_and_bias_for_sensor_imperfections(theta_gyr)
    Rm_gyro_to_acc = get_Rm_gyro_to_acc(theta_gyr)
    for i, _ in enumerate(ang_velocities):
        # meas = C @ w + b
        # inv(C) @ meas = w  + inv(C) @ b
        # w = inv(C) @ meas - inv(C) @ b
        ang_velocities[i] = Rm_gyro_to_acc @ (Cg @ ang_velocities[i] + bg + np.random.normal(0, 0.001, 3))
        accelerations[i] = Ca @ (accelerations[i]) + ba + np.random.normal(0, 0.04, 3)
        
    return ang_velocities, accelerations, standstill, orientations_true

## Acc calibration functions

In [4]:
def residual_acc(theta, accs, idxs, least_squares = True):
    C, b = build_matrix_and_bias_for_sensor_imperfections(theta)
    Cm = np.linalg.inv(C)
    
    z = np.zeros(3 * np.sum(idxs))
    ss_counter = 0;
    for i, ss in enumerate(idxs):
        if ss:
            acc = Cm @ accs[i].T - Cm @ b
            roll = np.arctan2(acc[1], acc[2])
            pitch = np.arctan2(-acc[0], np.sqrt(acc[2]**2 + acc[1]**2))

            u = 9.81 * np.array([-np.sin(pitch),
                                    np.cos(pitch)*np.sin(roll),
                                    np.cos(pitch)*np.cos(roll)])
            residual = u - acc
            z[2*ss_counter]     = residual[0]
            z[2*ss_counter + 1] = residual[1]
            z[2*ss_counter + 2] = residual[2]
            ss_counter += 1
           
    if least_squares:
        return z.flatten()
    else:
        return z.flatten() @ z.flatten()
    
def find_calib_params_acc(least_squares, residual, theta, accelerations, idxs_standstill):
    res = optimize.least_squares(residual_acc, theta, 
                                 args=(accelerations,
                                       idxs_standstill,
                                       least_squares,),
                                 max_nfev = 25,
                                 x_scale = [10., 10., 10., 10., 10., 10., 1., 1., 1.],
                                 method='trf', loss='soft_l1',
                                 bounds = [
                                       (-0.11, -0.11, -0.11, -0.11, -0.11, -0.11, -1.1, -1.1, -1.1),
                                       (0.11,   0.11,  0.11,  0.11,  0.11,  0.11,  1.1,  1.1,  1.1)],
        )
    return res.x

# Gyroscope calibration functions

In [5]:
def skew(v):
    if len(v) == 4:
        v = v[:3]/v[3]
    skv = np.roll(np.roll(np.diag(v.flatten()), 1, 1), -1, 0)
    return skv - skv.T

def residual_gyr(theta, gyrs, accs, standstill_flags, least_squares = True):
    C, b = build_matrix_and_bias_for_sensor_imperfections(theta)
    Cm = np.linalg.inv(C)
    
    gyro_to_acc = get_Rm_gyro_to_acc(theta)
    Rm = np.linalg.inv(gyro_to_acc)
    
    standstill_changes = np.hstack((0, np.diff(standstill_flags)))
    motion_starts = np.where(standstill_changes == -1)
    motion_ends = np.where(standstill_changes == 1)
    
    motion_start_end_idxs = []
    for s, e in zip(*motion_starts, *motion_ends):
        motion_start_end_idxs.append([s - 5, e + 5])
    
    z = np.zeros(2 * len(motion_start_end_idxs))
    prev_idx_motion_end = 0
    for i, (idx_motion_start, idx_motion_end) in enumerate(motion_start_end_idxs):
        acc_start = np.mean(accs[prev_idx_motion_end:idx_motion_start,:], axis=0)
        
        roll_start_acc = np.arctan2(acc_start[1], acc_start[2])
        pitch_start_acc = np.arctan2(-acc_start[0], np.sqrt(acc_start[2]**2 + acc_start[1]**2))
        yaw_start = 0.0
        
        gyr = gyrs[idx_motion_start:idx_motion_end,:]
        q = euler_to_quaternion(roll_start_acc, pitch_start_acc, yaw_start)
        
        for w in gyr:
            w_b = Cm @ Rm @ w - Cm @ b
            q_upd = Quaternion.exactFromOmega((w_b) * dt)
            q = q.prod(q_upd)

        roll_end_gyr, pitch_end_gyr,_ = quaternion_to_euler(q.q)
        
        if i < len(motion_start_end_idxs) - 1:
            next_idx_motion_start = motion_start_end_idxs[i+1][0]
        else:
            next_idx_motion_start = -1

        acc_end = np.mean(accs[idx_motion_end:next_idx_motion_start], axis=0)
        roll_end_acc = np.arctan2(acc_end[1], acc_end[2])
        pitch_end_acc = np.arctan2(-acc_end[0], np.sqrt(acc_end[2]**2 + acc_end[1]**2))
        
        ori_diff_gyr = np.array([[roll_end_gyr,
                                 pitch_end_gyr]])
        ori_diff_acc = np.array([[roll_end_acc,
                                 pitch_end_acc]])
        
        qgyr = euler_to_quaternion(roll_end_gyr, pitch_end_gyr, 0.0)
        qacc = euler_to_quaternion(roll_end_acc, pitch_end_acc, 0.0)
        qdiff = qacc.prod(qgyr.conj())
        euldiff = quaternion_to_euler(qdiff.q)
        
        z[2*i]     = euldiff[0]
        z[2*i + 1] = euldiff[1]
        
        prev_idx_motion_end = idx_motion_end
           
    if least_squares:
        return z.flatten()
    else:
        return z.flatten() @ z.flatten()
    

def find_calib_params_gyr(least_squares, residual, theta, ang_velocities, accelerations, standstill_flags):
    res = optimize.least_squares(
            residual, 
            theta, 
            args=(ang_velocities, 
                  accelerations,
                  standstill_flags,
                  least_squares,),
            max_nfev = 50,
            x_scale = [10., 10., 10., 10., 10., 10., 10., 10., 10., 10, 10, 10],
            method='trf', loss='soft_l1',
            bounds = [
                    (-0.11, -0.11, -0.11, -0.11, -0.11, -0.11, -0.11, -0.11, -0.11, -0.11, -0.11, -0.11),
                    (0.11,   0.11,  0.11,  0.11,  0.11,  0.11,  0.11,  0.11,  0.11,  0.11,  0.11,  0.11)],
        )
    return res.x

## One Monte-Carlo simulation cycle

In [6]:
def monte_carlo_cycle(N_samples, dt, theta_acc, theta_gyr, randomized_rotations, plot):
    fail = 0
    
    simulation_results = {}
    simulation_results['theta_acc_generated'] = theta_acc
    simulation_results['theta_gyr_generated'] = theta_gyr

    # generate data
    roll, pitch, yaw = np.deg2rad([-150, -75, -150])
    yaw_increment = np.deg2rad(18)
    
    angs, accs, ss, orientations_true = generate_data(roll, pitch, yaw, yaw_increment, theta_acc, theta_gyr,
                                  N_samples, dt, randomized_rotations)

    idxs_standstill = ss > 0
    idxs_motion = ss < 1e-8
    
    if plot:
        fig, ax = plt.subplots(2, 1, figsize=(20, 9))
        ax[0].plot(np.linalg.norm(accs, axis=1))
        ax[0].plot(np.arange(0, len(ss))[idxs_standstill], ss[idxs_standstill] + 10.0, linestyle='none', marker=',', alpha=0.9, color='green')
        ax[0].plot(np.arange(0, len(ss))[idxs_motion], ss[idxs_motion] + 10.0, linestyle='none', marker=',', alpha=0.9, color='red')
        ax[1].plot(angs)
        plt.show()

    # find accelerometer calibration parameters and calibrate accel measurements
    theta_found_acc = np.array([0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0])
    time_start = time.time()
    theta_found_acc = find_calib_params_acc(True, residual_acc, theta_found_acc, accs, idxs_standstill)
    time_end = time.time()

    print("ACC calibration done in: ", time_end - time_start)
    print(theta_acc)
    print(theta_found_acc)
    print(np.abs(theta_found_acc - theta_acc))

    accs_calibrated = calibrate_data(accs, theta_found_acc)

    if plot:
        fig, ax = plt.subplots(1, 1, figsize=(20, 5))
        ax.plot(np.linalg.norm(accs, axis=1))
        ax.plot(np.linalg.norm(accs_calibrated, axis=1))
        ax.legend(["Calibrated norm"])
        plt.show()

    # find gyroscope calibration parameters
    theta_found_gyr = np.array([0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0])
    theta_found_gyr[-6:-3] = np.mean(angs[0:N_samples,:], axis=0)
    print("start theta:", theta_found_gyr)
    time_start = time.time()
    theta_found_gyr = find_calib_params_gyr(True, residual_gyr, theta_found_gyr, angs, accs_calibrated, ss)
    time_end = time.time()

    print("GYR calibration done in: ", time_end - time_start)
    print(theta_gyr)
    print(theta_found_gyr)
    print(np.abs(theta_found_gyr - theta_gyr))

    df = residual_gyr(theta_found_gyr, 
             angs, 
             accs_calibrated,
             ss)
    print("Gyroscope residuals: ", np.sum(np.rad2deg(df**2)))
    
    if np.sum(np.rad2deg(df**2)) > 1.0:
        fail = 1
        print("Calibration failed!")
        
    simulation_results['theta_acc_found'] = theta_found_acc
    simulation_results['theta_gyr_found'] = theta_found_gyr
    simulation_results['residual_deg'] = np.sum(np.rad2deg(df**2))
    simulation_results['fail'] = fail
    
    return simulation_results

# Monte carlo simulations

In [7]:
fails = 0
N_samples = 100
dt = 0.01
randomized_rotations = True
plot = False

simulation_results = {}

for i in range(0, 5):
    theta_acc = np.random.randint(100, size=9)  / np.array([1000* np.random.choice([-1,1]), 1000* np.random.choice([-1,1]), 1000* np.random.choice([-1,1]), 
                                                            1000* np.random.choice([-1,1]), 1000* np.random.choice([-1,1]), 1000* np.random.choice([-1,1]), 100* np.random.choice([-1,1]), 100* np.random.choice([-1,1]), 100* np.random.choice([-1,1])])
    theta_gyr = np.random.randint(100, size=12) / np.array([1000* np.random.choice([-1,1]), 1000* np.random.choice([-1,1]), 1000* np.random.choice([-1,1]), 1000* np.random.choice([-1,1]), 1000* np.random.choice([-1,1]), 1000* np.random.choice([-1,1]), 
                                                            1000* np.random.choice([-1,1]), 1000* np.random.choice([-1,1]), 1000* np.random.choice([-1,1]), 1000* np.random.choice([-1,1]), 1000* np.random.choice([-1,1]), 1000* np.random.choice([-1,1])])
                                                                
    simulation_results[i] = monte_carlo_cycle(N_samples, dt, theta_acc, theta_gyr, randomized_rotations, plot)

ACC calibration done in:  5.705077886581421
[-0.0510  0.0310 -0.0690 -0.0380  0.0840  0.0320 -0.6400  0.7300  0.9700]
[-0.0509  0.0313 -0.0693 -0.0379  0.0845  0.0316 -0.6408  0.7319  0.9688]
[ 0.0001  0.0003  0.0003  0.0001  0.0005  0.0004  0.0008  0.0019  0.0012]
start theta: [ 0.0000  0.0000  0.0000  0.0000  0.0000  0.0000 -0.0825 -0.0847  0.0793  0.0000  0.0000  0.0000]
GYR calibration done in:  53.33263444900513
[ 0.0720 -0.0730 -0.0910 -0.0670  0.0670  0.0780 -0.0940 -0.0710  0.0780  0.0870  0.0810  0.0740]
[ 0.0722 -0.0729 -0.0908 -0.0659  0.0669  0.0779 -0.0940 -0.0711  0.0780  0.0876  0.0807  0.0737]
[ 0.0002  0.0001  0.0002  0.0011  0.0001  0.0001  0.0000  0.0001  0.0000  0.0006  0.0003  0.0003]
Gyroscope residuals:  0.0011829962634328723
ACC calibration done in:  13.483844757080078
[ 0.0300 -0.0230  0.0490 -0.0840  0.0790 -0.0900 -0.6400  0.2700  0.0800]
[ 0.0302 -0.0231  0.0495 -0.0845  0.0792 -0.0900 -0.6392  0.2681  0.0867]
[ 0.0002  0.0001  0.0005  0.0005  0.0002  0.0000

## Load monte-carlo simulations dump

In [8]:
import pickle
# with open('simulation_results200.pickle', 'wb') as handle:
#     pickle.dump(simulation_results, handle, protocol=pickle.HIGHEST_PROTOCOL)

simulation_results = pickle.load(open('simulation_results200.pickle', 'rb'))

In [9]:
residual = {'acc_scale':[], 'acc_nonort':[], 'acc_bias':[],
            'gyr_scale':[], 'gyr_nonort':[], 'gyr_bias':[], 'gyr_to_acc':[]}

for i, sim in simulation_results.items():
    kx, ky, kz, cx, cy, cz, bx, by, bz = sim['theta_acc_generated'] - sim['theta_acc_found']
    residual['acc_scale'].append([kx, ky, kz])
    residual['acc_nonort'].append([cx, cy, cz])
    residual['acc_bias'].append([bx, by, bz])
    
    kx, ky, kz, cx, cy, cz, bx, by, bz, mx, my, mz = sim['theta_gyr_generated'] - sim['theta_gyr_found']
    residual['gyr_scale'].append([kx, ky, kz])
    residual['gyr_nonort'].append([cx, cy, cz])
    residual['gyr_bias'].append([bx, by, bz])
    residual['gyr_to_acc'].append([mx, my, mz])


Build table for latex

In [10]:
for ca, cg in zip(['acc_scale', 'acc_nonort', 'acc_bias', None], ['gyr_scale', 'gyr_nonort', 'gyr_bias', 'gyr_to_acc']):   
    if ca is not None:
        meana = np.around(np.mean(residual[ca], axis=0), 4)
        stda = np.around(np.std(residual[ca], axis=0), 4)
    else:
        meana = ["$-$", "$-$", "$-$"]
        stda = ["$-$", "$-$", "$-$"]
        unitsa = ""
    meang = np.around(np.mean(residual[cg], axis=0), 4)
    stdg = np.around(np.std(residual[cg], axis=0), 4)
    
    if ca == 'acc_scale':
        unitsa=""
    if cg == 'gyr_scale':
        unitsg=""
    
    if ca == 'acc_nonort':
        meana, stda = np.rad2deg(meana), np.rad2deg(stda)
        unitsa = "$^\\circ$"
    if cg == 'gyr_nonort':
        meang, stdg = np.rad2deg(meang), np.rad2deg(stdg)
        unitsg = "$^\\circ$"
    if cg == 'gyr_bias':
        meang, stdg = np.rad2deg(meang), np.rad2deg(stdg)
        unitsg = '$^\\circ/s$'
    if ca == "acc_bias":
        unitsa = '$m/s^2$'
    if cg == 'gyr_to_acc':
        meang, stdg = np.rad2deg(meang), np.rad2deg(stdg)
        unitsg = '$^\\circ$'
        
    if ca is not None:
        meana = np.around(meana, 4)
        stda = np.around(stda, 4)
    else:
        meana = ["$-$", "$-$", "$-$"]
        stda = ["$-$", "$-$", "$-$"]

    meang = np.around(meang, 4)
    stdg = np.around(stdg, 4)
    
    print(" & ", meana[0], " & ", stda[0], " & ", unitsa, " & ", meang[0], " & ", stdg[0], " & ", unitsg, " \\\\ ")
    print(" & ", meana[1], " & ", stda[1], " & ", unitsa, " & ", meang[1], " & ", stdg[1], " & ", unitsg, " \\\\ ")
    print(" & ", meana[2], " & ", stda[2], " & ", unitsa, " & ", meang[2], " & ", stdg[2], " & ", unitsg, " \\\\ ")

 &  -0.0  &  0.0002  &    &  0.0003  &  0.0005  &    \\ 
 &  -0.0001  &  0.0004  &    &  0.0003  &  0.0006  &    \\ 
 &  0.0  &  0.0004  &    &  0.0004  &  0.0021  &    \\ 
 &  -0.0057  &  0.0286  &  $^\circ$  &  -0.0057  &  0.1891  &  $^\circ$  \\ 
 &  0.0  &  0.0286  &  $^\circ$  &  -0.0115  &  0.1318  &  $^\circ$  \\ 
 &  -0.0  &  0.0344  &  $^\circ$  &  0.0115  &  0.0688  &  $^\circ$  \\ 
 &  -0.0003  &  0.0019  &  $m/s^2$  &  -0.0172  &  0.0344  &  $^\circ/s$  \\ 
 &  -0.0  &  0.0031  &  $m/s^2$  &  0.0  &  0.0286  &  $^\circ/s$  \\ 
 &  -0.0002  &  0.0031  &  $m/s^2$  &  0.0  &  0.0229  &  $^\circ/s$  \\ 
 &  $-$  &  $-$  &    &  -0.0  &  0.0974  &  $^\circ$  \\ 
 &  $-$  &  $-$  &    &  -0.0  &  0.0286  &  $^\circ$  \\ 
 &  $-$  &  $-$  &    &  -0.0057  &  0.0401  &  $^\circ$  \\ 


# Calibration using real data from MIMU2.5

In [11]:
from IPython.display import set_matplotlib_formats
import matplotlib
font = {'family' : 'Times New Roman',
        'weight' : 'normal',
        'size'   : 10}
plt.rc('font', **font)

set_matplotlib_formats('pdf')

mimu_data = np.genfromtxt("mimu2.5.icosahedron.log", delimiter=' ', usecols=(4, 6, 7, 8, 9, 10, 11, 12))

results = {}

for ii in range(0, 5):
    print("IMU: ", ii)
    results[ii] = {}
    imu1 = mimu_data[mimu_data[:,0] == ii]
    imu1[:,2:5] *= 9.81
    imu1[:,5:8] *= np.deg2rad(1)

    standstill = np.zeros(len(imu1))
    counter_after_motion = 0
    for i, m in enumerate(imu1):
        if np.linalg.norm(m[5:8]) < 0.13:
            counter_after_motion += 1
            if counter_after_motion > 60:
                standstill[i] = 1
        else:
            standstill[i] = 0
            standstill[i-60:i] = 0
            counter_after_motion = 0

    imu1 = imu1[100:-200,:]
    standstill = standstill[100:-200]

    print("IMU data plots")
    fig, ax = plt.subplots(2, 1, figsize=(20, 9))
    ax[0].plot(imu1[:,1], imu1[:, 2:5])
    ax[1].plot(imu1[:,1], imu1[:, 5:8])
    ax[1].plot(imu1[:,1], standstill)
    ax[0].legend(["ax", "ay", "az"])
    ax[1].legend(["wx", "wy", "wz"])
    plt.show()

    accs = imu1[:,2:5]
    angs = imu1[:,5:8]

    print("Imu data plots with standstills")
    fig, ax = plt.subplots(2, 1, figsize=(20, 9))
    ax[0].plot(np.linalg.norm(accs, axis=1))
    idxs_standstill = standstill > 0
    idxs_motion = standstill < 1e-8
    ax[0].plot(np.arange(0, len(standstill))[idxs_standstill], standstill[idxs_standstill] + 10.0, linestyle='none', marker=',', alpha=0.9, color='green')
    ax[0].plot(np.arange(0, len(standstill))[idxs_motion], standstill[idxs_motion] + 10.0, linestyle='none', marker='.', alpha=0.9, color='red')
    ax[1].plot(angs)
    plt.show()

    # find accelerometer calibration parameters and calibrate accel measurements
    theta_found_acc = np.array([0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0])
    time_start = time.time()
    theta_found_acc = find_calib_params_acc(True, residual_acc, theta_found_acc, accs, idxs_standstill)
    time_end = time.time()

    print("ACC calibration done in: ", time_end - time_start)
    print(theta_found_acc)

    accs_calibrated = calibrate_data(accs[idxs_standstill], theta_found_acc)

    print("Uncalibrated and calibrated accel norm plots")
    fig, ax = plt.subplots(1, 1, figsize=(8, 3))
    times = np.arange(0, len(accs_calibrated)) * 0.01
    ax.plot(times, np.linalg.norm(accs[idxs_standstill], axis=1), alpha = 0.5)
    ax.plot(times, np.linalg.norm(accs_calibrated, axis=1), alpha = 0.5)
    ax.legend(["Uncalibrated norm", "Calibrated norm"])
    ax.set(xlabel='$time, s$', ylabel='$m/s^2$')
    plt.show()

    accs_calibrated = calibrate_data(accs, theta_found_acc)

    # find gyroscope calibration parameters
    theta_found_gyr = np.array([0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0])
    theta_found_gyr[-6:-3] = np.mean(angs[0:N_samples,:], axis=0)
    print("start theta:", theta_found_gyr)

    df= residual_gyr(theta_found_gyr, 
             angs, 
             accs_calibrated,
             standstill, True)
    print("Gyroscope residuals before calibration: ", np.sum(np.rad2deg(df)**2))

    time_start = time.time()
    theta_found_gyr = find_calib_params_gyr(True, residual_gyr, theta_found_gyr, angs, accs_calibrated, standstill)
    time_end = time.time()

    print("GYR calibration done in: ", time_end - time_start)
    print(theta_found_gyr)

    
    df = residual_gyr(theta_found_gyr, 
             angs, 
             accs_calibrated,
             standstill, True)
    print("Gyroscope residuals: ", np.sum(np.rad2deg(df)**2))
    plt.show()
    
    results[ii]['acc_theta'] = theta_found_acc
    results[ii]['gyr_theta'] = theta_found_gyr

IMU:  0
IMU data plots


<Figure size 1440x648 with 2 Axes>

Imu data plots with standstills


<Figure size 1440x648 with 2 Axes>

ACC calibration done in:  13.66391634941101
[ 0.0036  0.0032  0.0065  0.0021  0.0004  0.0055  0.1029  0.0967  0.3442]
Uncalibrated and calibrated accel norm plots


...

Imu data plots with standstills


<Figure size 1440x648 with 2 Axes>

ACC calibration done in:  38.667821407318115
[ 0.0025  0.0029  0.0080  0.0010  0.0000  0.0033  0.0700  0.0363  0.1817]
Uncalibrated and calibrated accel norm plots


<Figure size 576x216 with 1 Axes>

start theta: [ 0.0000  0.0000  0.0000  0.0000  0.0000  0.0000 -0.0189  0.0101  0.0249  0.0000  0.0000  0.0000]
Gyroscope residuals before calibration:  5.768199825700678
GYR calibration done in:  97.77472400665283
[ 0.0023  0.0057  0.0085  0.0014  0.0031  0.0087 -0.0184  0.0071  0.0252  0.0014 -0.0039  0.0013]
Gyroscope residuals:  0.186648051949433


Build table for latex:

In [12]:
pos = {'sx' : 0, 'sy':1, 'sz':2, 
      'nox':3, 'noy':4, 'noz':5,
      'bx':6, 'by':7, 'bz':8,
      'mx':9, 'my':10, 'mz':11}
conv = {'sx' : lambda x: x * 100, 'sy':lambda x: x * 100, 'sz':lambda x: x * 100, 
      'nox':np.rad2deg, 'noy':np.rad2deg, 'noz':np.rad2deg,
      'bx':lambda x: x, 'by': lambda x: x, 'bz': lambda x:x,
      'mx':np.rad2deg, 'my':np.rad2deg, 'mz':np.rad2deg}

for param in ['sx', 'sy', 'sz', 'nox', 'noy', 'noz', 'bx', 'by', 'bz', 'mx', 'my', 'mz']:
    for sensor in ['a', 'g']:
        for i in range(0, 5):
            if sensor == 'a':
                params = results[i]['acc_theta']
            else:
                params = results[i]['gyr_theta']
            if pos[param] < len(params):
                v = np.around(conv[param](params[pos[param]]), 3)
            else:
                v = "$-$"
                
            if param[0] == 'b' and sensor == 'g':
                v = np.rad2deg(v)
                v = np.around(v, 3)
                
            print(v, " & ", end="")
    print("\\\\")

0.363  & 0.471  & 0.382  & 0.263  & 0.251  & 0.041  & 0.007  & -0.058  & 0.227  & 0.226  & \\
0.315  & 0.482  & 0.355  & 0.448  & 0.286  & 0.457  & 0.26  & 0.277  & 0.599  & 0.57  & \\
0.647  & 0.932  & 0.78  & 0.721  & 0.804  & 0.826  & -0.179  & 0.242  & 0.308  & 0.853  & \\
0.123  & -0.284  & 0.26  & -0.009  & 0.056  & -0.034  & -0.639  & 0.15  & -0.105  & 0.08  & \\
0.02  & -0.01  & -0.012  & -0.028  & 0.0  & -0.12  & 0.21  & -0.072  & 0.025  & 0.178  & \\
0.317  & 0.145  & 0.282  & -0.104  & 0.191  & 0.806  & 0.262  & 0.876  & 0.072  & 0.497  & \\
0.103  & 0.09  & 0.096  & 0.065  & 0.07  & 1.146  & -0.573  & 0.573  & -1.261  & -1.031  & \\
0.097  & 0.07  & 0.008  & 0.092  & 0.036  & -0.401  & 1.089  & -0.344  & 1.031  & 0.401  & \\
0.344  & 0.338  & -0.045  & -0.009  & 0.182  & 1.261  & 0.286  & 1.261  & 4.813  & 1.432  & \\
$-$  & $-$  & $-$  & $-$  & $-$  & 0.03  & -0.565  & 0.142  & -0.102  & 0.077  & \\
$-$  & $-$  & $-$  & $-$  & $-$  & -0.364  & 0.013  & -0.482  & -0.129  & 

# Build plots to show how gyro errors affect orientation estimate

In [15]:
def residual_gyr_debug(theta, gyrs, accs, standstill_flags, least_squares = True):
    C, b = build_matrix_and_bias_for_sensor_imperfections(theta)
    Cm = np.linalg.inv(C)
    
    gyro_to_acc = get_Rm_gyro_to_acc(theta)
    Rm = np.linalg.inv(gyro_to_acc)
    
    standstill_changes = np.hstack((0, np.diff(standstill_flags)))
    motion_starts = np.where(standstill_changes == -1)
    motion_ends = np.where(standstill_changes == 1)
    
    motion_start_end_idxs = []
    for s, e in zip(*motion_starts, *motion_ends):
        motion_start_end_idxs.append([s, e])
    
    z = np.zeros(2 * len(motion_start_end_idxs))
    prev_idx_motion_end = 0
    orientations = []
    acc_orientations = []
    for i, (idx_motion_start, idx_motion_end) in enumerate(motion_start_end_idxs):
        if i == 0:
            acc_start = np.mean(accs[prev_idx_motion_end:idx_motion_start,:], axis=0)
        
            roll_start_acc = np.arctan2(acc_start[1], acc_start[2])
            pitch_start_acc = np.arctan2(-acc_start[0], np.sqrt(acc_start[2]**2 + acc_start[1]**2))
            yaw_start = 0.0
            
            q = euler_to_quaternion(roll_start_acc, pitch_start_acc, yaw_start)
            acc_orientations.append([roll_start_acc, pitch_start_acc, yaw_start])
            
        gyr = gyrs[idx_motion_start:idx_motion_end,:]
        
        for w in gyr:
            w_b = Cm @ Rm @ w - Cm @ b
            q_upd = Quaternion.exactFromOmega((w_b) * dt)
            q = q.prod(q_upd)
            orientations.append(quaternion_to_euler(q.q))

        roll_end_gyr, pitch_end_gyr,_ = quaternion_to_euler(q.q)
        
        if i < len(motion_start_end_idxs) - 1:
            next_idx_motion_start = motion_start_end_idxs[i+1][0]
        else:
            next_idx_motion_start = -1

        if i == len(motion_start_end_idxs) - 1:
            acc_end = np.mean(accs[idx_motion_end:next_idx_motion_start], axis=0)
            roll_end_acc = np.arctan2(acc_end[1], acc_end[2])
            pitch_end_acc = np.arctan2(-acc_end[0], np.sqrt(acc_end[2]**2 + acc_end[1]**2))
        
            acc_orientations.append([roll_end_acc, pitch_end_acc, 0.0])
        
            ori_diff_gyr = np.array([[roll_end_gyr,
                                 pitch_end_gyr]])
            ori_diff_acc = np.array([[roll_end_acc,
                                 pitch_end_acc]])
        
            qgyr = euler_to_quaternion(roll_end_gyr, pitch_end_gyr, 0.0)
            qacc = euler_to_quaternion(roll_end_acc, pitch_end_acc, 0.0)
            qdiff = qacc.prod(qgyr.conj())
            euldiff = quaternion_to_euler(qdiff.q)
            
        prev_idx_motion_end = idx_motion_end
        
    return euldiff, orientations, acc_orientations

In [16]:
fails = 0
N_samples = 100
dt = 0.01
randomize = True
plot = False

simulation_results = {}

theta_acc = np.array([ 0.0025,  0.0029,  0.0080,  0.0010,  0.0000,  0.0033,  0.0700,  0.0363,  0.1817])
theta_gyr = np.array([ 0.0023,  0.0057,  0.0085,  0.0014,  0.0031,  0.0087, -0.0184,  0.0071,  0.0252,  0.0014, -0.0039,  0.0013])

# generate data
roll, pitch, yaw = np.deg2rad([-150, -75, -150])
yaw_increment = np.deg2rad(18)

angs, accs, ss, oris_true = generate_data(roll, pitch, yaw, yaw_increment, theta_acc, theta_gyr,
                              N_samples, dt, randomize)

idxs_standstill = ss > 0
idxs_motion = ss < 1e-8

# find accelerometer calibration parameters and calibrate accel measurements
theta_found_acc = np.array([0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0])
time_start = time.time()
theta_found_acc = find_calib_params_acc(True, residual_acc, theta_found_acc, accs, idxs_standstill)
time_end = time.time()

print("ACC calibration done in: ", time_end - time_start)
print(theta_acc)
print(theta_found_acc)
print(np.abs(theta_found_acc - theta_acc))

accs_calibrated = calibrate_data(accs, theta_found_acc)

# find gyroscope calibration parameters
theta_found_gyr = np.array([0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0])
    
df, raw_ori, raw_ori_acc = residual_gyr_debug(theta_found_gyr, 
         angs, 
         accs_calibrated,
         ss)
    
theta_found_gyr[-6:-3] = np.mean(angs[0:N_samples,:], axis=0)

df, bef_ori, bef_ori_acc = residual_gyr_debug(theta_found_gyr, 
         angs, 
         accs_calibrated,
         ss)
    
print("start theta:", theta_found_gyr)
time_start = time.time()
theta_found_gyr = find_calib_params_gyr(True, residual_gyr, theta_found_gyr, angs, accs_calibrated, ss)
time_end = time.time()

print("GYR calibration done in: ", time_end - time_start)
print(theta_gyr)
print(theta_found_gyr)
print(np.abs(theta_found_gyr - theta_gyr))

df, aft_ori, aft_ori_acc = residual_gyr_debug(theta_found_gyr, 
         angs, 
         accs_calibrated,
         ss)
print("Gyroscope residuals: ", np.sum(np.rad2deg(df)**2))

ACC calibration done in:  15.334876298904419
[ 0.0025  0.0029  0.0080  0.0010  0.0000  0.0033  0.0700  0.0363  0.1817]
[ 0.0026  0.0025  0.0084  0.0012  0.0002  0.0033  0.0691  0.0339  0.1859]
[ 0.0001  0.0004  0.0004  0.0002  0.0002  0.0000  0.0009  0.0024  0.0042]
start theta: [ 0.0000  0.0000  0.0000  0.0000  0.0000  0.0000 -0.0185  0.0072  0.0252  0.0000  0.0000  0.0000]
GYR calibration done in:  68.13974833488464
[ 0.0023  0.0057  0.0085  0.0014  0.0031  0.0087 -0.0184  0.0071  0.0252  0.0014 -0.0039  0.0013]
[ 0.0004  0.0041  0.0090  0.0018  0.0037  0.0071 -0.0160  0.0066  0.0254  0.0020 -0.0034  0.0017]
[ 0.0019  0.0016  0.0005  0.0004  0.0006  0.0016  0.0024  0.0005  0.0002  0.0006  0.0005  0.0004]
Gyroscope residuals:  0.7190537972535691


In [17]:
oris_true_eul = []
for q in oris_true[1:]:
    oris_true_eul.append(quaternion_to_euler(q))
oris_true_eul = np.array(oris_true_eul)

In [18]:
mot = np.logical_not(ss.astype(bool))
sel_oris = oris_true_eul[mot]

diff_true_raw_eulers = []
diff_true_bef_eulers = []
diff_true_aft_eulers = []

for tr, raw, bef, aft in zip(sel_oris, raw_ori, bef_ori, aft_ori):
    q_tr = euler_to_quaternion(*tr)
    q_raw = euler_to_quaternion(*raw)
    q_bef = euler_to_quaternion(*bef)
    q_aft = euler_to_quaternion(*aft)
    
    diff_true_raw = q_raw.prod(q_tr.conj())
    diff_true_bef = q_bef.prod(q_tr.conj())
    diff_true_aft = q_aft.prod(q_tr.conj())
    
    diff_true_raw_eul = quaternion_to_euler(diff_true_raw.q)
    diff_true_bef_eul = quaternion_to_euler(diff_true_bef.q)
    diff_true_aft_eul = quaternion_to_euler(diff_true_aft.q)
    
    diff_true_raw_eulers.append(diff_true_raw_eul)
    diff_true_bef_eulers.append(diff_true_bef_eul)
    diff_true_aft_eulers.append(diff_true_aft_eul)

In [19]:
times = np.arange(0, len(sel_oris)) * 0.01
fig, ax = plt.subplots(1, 1, figsize=(8, 3))
ax.plot(times, np.rad2deg(oris_true_eul)[mot])
ax.legend(["$\phi$", '$\\theta$', "$\psi$"])
ax.set(xlabel="$time,~sec$", ylabel="$angle,~^\circ$")
print("Plot true euler orientations")

Plot true euler orientations


<Figure size 576x216 with 1 Axes>

In [20]:
diff_true_raw_eulers_deg = np.rad2deg(diff_true_raw_eulers)
diff_true_bef_eulers_deg = np.rad2deg(diff_true_bef_eulers)
diff_true_aft_eulers_deg = np.rad2deg(diff_true_aft_eulers)


axis = 0
fig, ax = plt.subplots(3, 1, figsize=(8, 6))
ax[0].plot(times, diff_true_raw_eulers_deg[:,axis] - diff_true_raw_eulers_deg[0, axis])
ax[0].plot(times, diff_true_bef_eulers_deg[:,axis] - diff_true_raw_eulers_deg[0, axis])
ax[0].plot(times, diff_true_aft_eulers_deg[:,axis] - diff_true_raw_eulers_deg[0, axis])
ax[0].legend(["Case #1", "Case #2", "Case #3"], ncol=3, loc='lower left')
ax[0].set(xlabel="$time,~sec$", ylabel="$orientation~error,~^\circ$")
ax[axis].set_title("roll angle error, $\delta\phi$")

axis = 1
ax[axis].plot(times, diff_true_raw_eulers_deg[:,axis] - diff_true_raw_eulers_deg[0, axis])
ax[axis].plot(times, diff_true_bef_eulers_deg[:,axis] - diff_true_raw_eulers_deg[0, axis])
ax[axis].plot(times, diff_true_aft_eulers_deg[:,axis] - diff_true_raw_eulers_deg[0, axis])
ax[axis].legend(["Case #1", "Case #2", "Case #3"], ncol=3, loc='lower left')
ax[axis].set(xlabel="$time,~sec$", ylabel="$orientation~error,~^\circ$")
ax[axis].set_title("pitch angle error, $\delta\\theta$")

axis = 2
ax[axis].plot(times, diff_true_raw_eulers_deg[:,axis] - diff_true_raw_eulers_deg[0, axis])
ax[axis].plot(times, diff_true_bef_eulers_deg[:,axis] - diff_true_raw_eulers_deg[0, axis])
ax[axis].plot(times, diff_true_aft_eulers_deg[:,axis] - diff_true_raw_eulers_deg[0, axis])
ax[axis].legend(["Case #1", "Case #2", "Case #3"], ncol=3, loc='lower left')
ax[axis].set(xlabel="$time,~sec$", ylabel="$orientation~error,~^\circ$")
ax[axis].set_title("yaw angle error, $\delta\psi$")

print("Plot effect of gyroscope errors on orientation estimates")
plt.tight_layout()

# handles, labels = ax[2].get_legend_handles_labels()
# fig.legend(handles, labels, loc='upper center')

Plot effect of gyroscope errors on orientation estimates


<Figure size 576x432 with 3 Axes>